# Visualizing spatial data with CARTOframes

In this notebook we will learn of how to visualize on a map different types of spatial (point-referenced data, areal data, point patterns) data using CARTOframes.

For more info on setting your credentials, reading/uploading data from/to CARTO, styling you maps and add legends and pop-ups, see https://carto.com/developers/cartoframes/reference/.

## Let's first access the CARTO account where the data we are going to use are stored.

We will use some public datasets stored in the CARTO account <i>ebook-sds</i>. Since the datasets are public, we don't need to specify the credentials (username and API KEY).

In [1]:
from cartoframes.auth import set_default_credentials, Credentials
import seaborn as sns
import warnings

warnings.filterwarnings("ignore")

# pull data from my account
set_default_credentials("ebook-sds")

sns.set()

## Point-referenced data

### Let's plot a map of Sea Surface Temperature (SST) in situ data from the International Comprehensive Ocean-Atmosphere Data Set (https://icoads.noaa.gov) 

#### Let's first read in the data and create a geopandas dataframe for the SST for each record 

In [2]:
import pandas as pd
import geopandas as gpd
from cartoframes import read_carto

data_pf = read_carto("icoads_may3to5_2019")
data_pf.head()

cartodb_id                the_geom         lon        lat       date  hour  \
0           1  POINT (178.600 80.820)  178.600006  80.820000 2019-05-01   0.0   
1           2   POINT (29.000 71.130)   29.000000  71.129997 2019-05-01   0.0   
2           3  POINT (207.180 70.900)  207.179993  70.900002 2019-05-01   0.0   
3           4  POINT (206.010 70.820)  206.009995  70.820000 2019-05-01   0.0   
4           5  POINT (208.250 70.550)  208.250000  70.550003 2019-05-01   0.0   

   sst  
0 -5.6  
1  4.2  
2 -3.8  
3 -7.0  
4 -5.4

**Note**: Data is directly mappable if it has a geometry column (e.g., is a GeoDataFrame) or has latitude and longitude columns.

In [3]:
from cartoframes.viz import Map, Layer, color_continuous_style,color_continuous_legend,basemaps
from matplotlib import cm

viridis = cm.get_cmap("viridis", 9)

Map(
    Layer(data_pf,
        style = color_continuous_style('sst',
                               palette=[f"rgb({c[0]}, {c[1]}, {c[2]})" for c in 255 * viridis.colors]),
        legends=color_continuous_legend(title="Sea Surface Temperature (°C)",
                                        description='ICOADS 1-3 May 2019'
        )
    ),
    basemap=basemaps.darkmatter,
)

The history saving thread hit an unexpected error (OperationalError('database is locked')).History will not be written to the database.


# Areal data

## Let's plot a map of the total population by Census Tracks in NYC using data from the US Census (https://www.census.gov/)

### Let's first read in the data

In [4]:
import geopandas as gpd

data_poly = read_carto("ny_census_tracts_2010")

In [5]:
data_poly.head()

cartodb_id                                           the_geom  \
0       44813  MULTIPOLYGON (((-73.92957 40.59682, -73.93503 ...   
1       46468  MULTIPOLYGON (((-73.85292 40.74617, -73.85887 ...   
2       48039  MULTIPOLYGON (((-73.89390 40.82364, -73.89193 ...   
3       44464  MULTIPOLYGON (((-73.90745 40.63928, -73.91037 ...   
4       45942  MULTIPOLYGON (((-73.85092 40.71047, -73.85565 ...   

         namelsad10   aland10  awater10   intptlat10    intptlon10  dp0010001  \
0  Census Tract 632  117438.0       0.0  +40.5997604  -073.9315683     1447.0   
1  Census Tract 415  170942.0       0.0  +40.7466051  -073.8565990     4278.0   
2  Census Tract 159  103416.0       0.0  +40.8223699  -073.8935569     2164.0   
3  Census Tract 958  234374.0       0.0  +40.6408221  -073.9116859     3456.0   
4  Census Tract 729  193202.0       0.0  +40.7128152  -073.8521724     1363.0   

   dp0010002  dp0010003  ...  dp0220001  dp0220002  dp0230001  dp0230002  \
0       49.0       59.0  ...     1153.0      281.0       2.17       1.91   
1      380.0      278.0  ...      964.0     3298.0       3.61       3.93   
2      151.0      145.0  ...       99.0     2065.0       3.41       3.17   
3      205.0      196.0  ...     1854.0     1583.0       3.19       2.89   
4       88.0       82.0  ...      990.0      364.0       2.76       2.56   

   shape_leng  shape_area           created_at           updated_at  \
0    0.018151    0.000012  2015-05-08T13:43:04  2015-05-08T15:02:25   
1    0.018358    0.000018  2015-05-08T13:43:04  2015-05-08T15:02:25   
2    0.014013    0.000011  2015-05-08T13:43:04  2015-05-08T15:02:25   
3    0.021789    0.000025  2015-05-08T13:43:04  2015-05-08T15:02:25   
4    0.018542    0.000021  2015-05-08T13:43:04  2015-05-08T15:02:25   

   dp0080018      geoid10  
0        0.0  36047063200  
1        1.0  36081041500  
2        2.0  36005015900  
3        1.0  36047095800  
4        0.0  36081072900  

[5 rows x 198 columns]

#### Let's plot the total population by Census Tracks

In [6]:
from cartoframes.viz import color_bins_style,color_bins_legend

Map(
    Layer(data_poly,
        style = color_bins_style('dp0010001',
                         bins=7,
                         opacity=0.5,
                         palette="bluyl",
                         stroke_color="transparent"),
        legends=color_bins_legend(title="Total population", 
                                  description='by Census Track')
        ),
    viewport={"zoom": 9.01, "lat": 40.767764, "lng": -73.777284},
    show_info=True
)

# Line Data

### Let's plot a map of flight tracks from NYC airports using data from the the [FAA Aircraft registry](http://www.faa.gov/licenses_certificates/aircraft_certification/aircraft_registry/releasable_aircraft_download/)

**Let's first read in the data**

In [7]:
data_line = read_carto("nyc_flights")

#### Let's plot the flight tracks by airport of arrival/departure

In [8]:
from cartoframes.viz import color_category_style, color_category_legend

Map(
    Layer(data_line,
        style = color_category_style('airport',
                         opacity=0.6),
        legends=color_category_legend(title="Destination/Arrival Airport")
    ),
    viewport={"zoom": 6.90, "lat": 40.864696, "lng": -73.962515},
    show_info=True
)

## Point patterns data
### Let's plot a map of the occurence of burglary and other thefts in London from the UK Police data (https://data.police.uk/data/)

In [9]:
data_pp = read_carto("uk_police_street_crimes_2019_04")

In [10]:
Map(
    Layer(data_pp,
        style = color_category_style('crime_type',
                         opacity=0.5),
        legends=color_category_legend(title="Burglary crimes",
                                     description = 'source: UK Police',
                                     footer = 'date: Apr 2019')
    ),
    viewport={"zoom": 9.27, "lat": 51.499978, "lng": -0.117578},
    show_info=True
)

## Publishing

With CARTO credentials, it is possible to publish to CARTO's platform and get a URL to share it.

However, since we don't have access to the credentials of the CARTO account used to store the public datasets used in this notebook, the following will throw an error ('Access denied').

In [11]:
# Make map referencing table in carto account

outmap = Map(
    Layer('uk_police_street_crimes_2019_04',
        style = color_category_style('crime_type',
                         opacity=0.5),
        legends=color_category_legend(title="Burglary crimes",
                                     description = 'source: UK Police',
                                     footer = 'date: Apr 2019')
    ),
    viewport={"zoom": 9.27, "lat": 51.499978, "lng": -0.117578},
    show_info=True
)

In [12]:
# Publish Map
outmap.publish(name='London Burglaries', password=None)

ForbiddenErrorException: Access denied